# Interoperation with ANDES

One of the most interesting feature of AMS is its interoperation with dynamic simulator ANDES.

Interoperation includes compatible case conversion and data exchange, thus it facilitates scheduling-dynamics co-simulation using AMS and ANDES.

In [1]:
import numpy as np

import andes
import ams

In [2]:
ams.config_logger(stream_level=20)

## Scheduling

In [3]:
sp = ams.load(ams.get_case('ieee14/ieee14_uced.xlsx'),
              setup=True,
              no_output=True,)

Parsing input file "/Users/jinningwang/work/miniconda3/envs/amsre/lib/python3.12/site-packages/ams/cases/ieee14/ieee14_uced.xlsx"...
Input file parsed in 0.0675 seconds.
System set up in 0.0013 seconds.


In [4]:
sp.RTED.init()

Building system matrices
Parsing OModel for <RTED>
Evaluating OModel for <RTED>
Finalizing OModel for <RTED>
<RTED> initialized in 0.0129 seconds.


True

In [5]:
sp.RTED.run(solver='CLARABEL')

<RTED> solved as optimal in 0.0119 seconds, converged in 10 iterations with CLARABEL.


True

## Convert to ANDES

The built-in ANDES interface can convert an AMS case to ANDES case in memory.

The bridge between AMS and converted ANDES is the shared power flow devices, Bus, PQ, PV, Slack, Line, and Shunt.

In [6]:
sa = sp.to_andes(setup=True,
                 addfile=andes.get_case('ieee14/ieee14_full.xlsx'))

Generating code for 1 models on 12 processes.


Parsing additional file "/Users/jinningwang/work/miniconda3/envs/amsre/lib/python3.12/site-packages/andes/cases/ieee14/ieee14_full.xlsx"...
Following PFlow models in addfile will be overwritten: <Bus>, <PQ>, <PV>, <Slack>, <Shunt>, <Line>, <Area>
Addfile parsed in 0.0336 seconds.
System converted to ANDES in 0.2209 seconds.
AMS system 0x3382b5340 is linked to the ANDES system 0x33bcfb260.


If you wish to add devices to the converted ANDES system, set `setup=False` to skip the ANDES setup process.

As indicated by the output information, in the conversion process, ANDES power flow devices will be overwritten by AMS ones, if exists.

Upon a successful conversion, you are ready to enjoy full capability of ANDES.

``help`` command can give a quick reference.

In [7]:
help(sp.to_andes)

Help on method to_andes in module ams.system:

to_andes(addfile=None, setup=False, no_output=False, default_config=True, verify=False, tol=0.001, **kwargs) method of ams.system.System instance
    Convert the AMS system to an ANDES system.

    A preferred dynamic system file to be added has following features:
    1. The file contains both power flow and dynamic models.
    2. The file can run in ANDES natively.
    3. Power flow models are in the same shape as the AMS system.
    4. Dynamic models, if any, are in the same shape as the AMS system.

    This function is wrapped as the ``System`` class method ``to_andes()``.
    Using the file conversion ``to_andes()`` will automatically
    link the AMS system instance to the converted ANDES system instance
    in the AMS system attribute ``dyn``.

    It should be noted that detailed dynamic simualtion requires extra
    dynamic models to be added to the ANDES system, which can be passed
    through the ``addfile`` argument.

    Para

## Interoperation with ANDES

In the interface class ``dyn``, the link table is stored in ``dyn.link``.

It describes the mapping relationships between power flow devices and dynamic devices.

In [8]:
sp.dyn.link

stg_idx bus_idx   syg_idx  gov_idx dg_idx rg_idx  gammap  gammaq
0  Slack_1       1  GENROU_1  TGOV1_1    NaN    NaN     1.0     1.0
1     PV_5       8  GENROU_5  TGOV1_5    NaN    NaN     1.0     1.0
2     PV_4       6  GENROU_4  TGOV1_4    NaN    NaN     1.0     1.0
3     PV_3       3  GENROU_3  TGOV1_3    NaN    NaN     1.0     1.0
4     PV_2       2  GENROU_2  TGOV1_2    NaN    NaN     1.0     1.0

### Send

As there is a gap between DC-based dispatch and AC-based TDS, a conversion is required to ensure the TDS initialization.

In [9]:
sp.RTED.dc2ac()

Parsing OModel for <ACOPF>
Evaluating OModel for <ACOPF>
Finalizing OModel for <ACOPF>
<ACOPF> initialized in 0.0083 seconds.
<ACOPF> solved in 0.1152 seconds, converged in 12 iterations with PYPOWER-PIPS.
<RTED> converted to AC.


True

In the RTED routine, there are two mapping dictionaries to define the data exchange, namely, `map1` for receiving data from ANDES and `map2` for sending data to ANDES.

In [10]:
sp.RTED.map2

OrderedDict([('vBus', ('Bus', 'v0')),
             ('ug', ('StaticGen', 'u')),
             ('pg', ('StaticGen', 'p0'))])

In [11]:
sp.dyn.send(adsys=sa, routine='RTED')

Send <RTED> results to ANDES <0x33bcfb260>...
*Send <vBus> to StaticGen.v0
Send <vBus> to Bus.v0
Send <ug> to StaticGen.u
Send <pg> to StaticGen.p0


True

### Run ANDES

Sometimes, the ANDES TDS initialization may fail due to inapproriate limits.

Here, we alleviate the `TGOV1` limit issue by enlarging the `Pmax` and `Pmin` to the same value.

In [12]:
sa.TGOV1.alter(src='VMAX', idx=sa.TGOV1.idx.v, value=100*np.ones(sa.TGOV1.n))
sa.TGOV1.alter(src='VMIN', idx=sa.TGOV1.idx.v, value=np.zeros(sa.TGOV1.n))

Run power flow.

In [13]:
sa.PFlow.run()

True

Try to init TDS.

In [14]:
_ = sa.TDS.init()

Run TDS.

In [15]:
sa.TDS.config.no_tqdm = True # disable progress bar
sa.TDS.run()

True

### Receive

In [16]:
sp.RTED.map1

OrderedDict([('ug', ('StaticGen', 'u')), ('pg0', ('StaticGen', 'p'))])

In [17]:
sp.dyn.receive(adsys=sa, routine='RTED')

Receive <ug> from SynGen.u
Receive <pg0> from SynGen.Pe


True

The RTED parameter ``pg0``, is retrieved from ANDES as the corresponding generator output power.

In [18]:
sp.RTED.pg0.v

array([0.48417982, 0.01000094, 0.02000094, 0.01000095, 1.79503641])